<a href="https://colab.research.google.com/github/abnormalPotassium/DATA620/blob/main/Project%202/Project2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Project 2: Moreno Crime Bipartite Analysis

By: Al Haque, Taha Ahmad


---
## Goal

This assignment's goal is to:
-  Identify a large 2-node network dataset—you can start with a dataset in a repository.  Your data should meet the criteria that it consists of ties between and not within two (or more) distinct groups.
-  Reduce the size of the network using a method such as the island method described in chapter 4 of social network analysis.
-  Infer unique characteristics about each group.


---
## Package Installation

Installing packages used through the semester from our requirements.txt in GitHub.

In [1]:
!pip install -r https://raw.githubusercontent.com/abnormalPotassium/DATA620/main/Environment/requirements.txt


---
## Dataset Loading

[Our data](http://konect.cc/networks/moreno_crime/) is collected by the University of California Irvine. It consists of
witnesses and perpetrators that were involved in crimes recorded in Moreno, California. There were 829 nodes consisting of people and there were 551 nodes consisting of crimes.

Initially we import the packages that we will need to both load, analyze, and plot our data.

In [2]:
import matplotlib.pyplot as plt
import pandas as pd
import re
from pyvis.network import Network
import networkx as nx
from networkx.algorithms import bipartite
from IPython.core.display import display, HTML

First we download the zipped dataset and then unzip it through terminal commands.

In [3]:
!curl -o moreno_crime.tar.bz2 http://konect.cc/files/download.tsv.moreno_crime.tar.bz2
!tar -xvjf moreno_crime.tar.bz2

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 11613  100 11613    0     0  32696      0 --:--:-- --:--:-- --:--:-- 32712
moreno_crime/
moreno_crime/meta.moreno_crime_crime
moreno_crime/README.moreno_crime
moreno_crime/rel.moreno_crime_crime.person.role
moreno_crime/ent.moreno_crime_crime.person.sex
moreno_crime/ent.moreno_crime_crime.person.name
moreno_crime/out.moreno_crime_crime


We build upon [another implementation](https://github.com/ericmjl/nxviz/blob/master/examples/datasets/crime.py) of reading this crime data below: We begin by reading the main file which links people to crimes and build a pandas dataframe from it. These will be our bipartite nodes which are connected by the edges of the role the person had in the crime which is read from the .role file. We utilize these nodes and edges to build an intial bipartite graph.

Afterwards we add additional attributes to our graph by reading the .gender and .name files to give each person node their gender and their name for possible further analysis. The genders are coded with 0 being female and 1 being male, so that is decoded for easier analysis. While the names are in a `LastnameFirstname` format which we split and reverse for easier reading.

In [4]:
df = pd.read_csv(
    "moreno_crime/out.moreno_crime_crime",
    sep=" ",
    skiprows=2,
    header=None,
)
df = df[[0, 1]]
df.columns = ["personID", "crimeID"]
df.index += 1

# Read in the role metadata
roles = pd.read_csv(
    "moreno_crime/rel.moreno_crime_crime.person.role",
    header=None,
)
roles.columns = ["roles"]
roles.index += 1

G = nx.Graph()
for r, d in df.join(roles).iterrows():
    pid = "p{0}".format(d["personID"])  # pid stands for "Person I.D."
    cid = "c{0}".format(d["crimeID"])  # cid stands for "Crime I.D."
    G.add_node(pid, bipartite="person")
    G.add_node(cid, bipartite="crime")
    G.add_edge(pid, cid, role=d["roles"])

gender = pd.read_csv(
    "moreno_crime/ent.moreno_crime_crime.person.sex",
    header=None,
)
gender.index += 1
for n, gender_code in gender.iterrows():
    nodeid = "p{0}".format(n)
    if gender_code[0]:
      gender_code[0] = "male"
    else:
      gender_code[0] = "female"
    G.nodes[nodeid]["gender"] = gender_code[0]

with open("moreno_crime/ent.moreno_crime_crime.person.name", 'r') as file:
    lines = []
    for line in file:
        line = line.strip()
        line = " ".join(re.split('(?<=.)(?=[A-Z])', line)[::-1])
        lines.append(line)

names = pd.DataFrame(lines)
names.index += 1
for n, person in names.iterrows():
    nodeid = "p{0}".format(n)
    G.nodes[nodeid]["name"] = person[0]

First let's check whether the Network is Bipartite in this case it returns True

In [5]:
nx.is_bipartite(G)

True

We can then see what our person nodes look like below with their attributes:

In [6]:
print(G.nodes["p1"], G.nodes["p7"])

{'bipartite': 'person', 'gender': 'male', 'name': 'Dennis Abel'} {'bipartite': 'person', 'gender': 'female', 'name': 'Martha Adams'}


Our crime nodes do not have any additional attributes on the otherhand:

In [7]:
print(G.nodes["c1"], G.nodes["c7"])

{'bipartite': 'crime'} {'bipartite': 'crime'}


We copy the members of each type of node within our graph for further analysis down the line.

In [8]:
crimes = [n for n, d in G.nodes(data = True) if d["bipartite"] == "crime"]
persons = [n for n, d in G.nodes(data = True) if d["bipartite"] == "person"]

---
## Initial Dataset Analysis

We quickly showcase a biadjacency matrix so we can see that our data has been properly loaded with adjacent neighbours between both the crimes and the people.

In [9]:
print("Biadjacency matrix")
print(bipartite.biadjacency_matrix(G, crimes, persons))

Biadjacency matrix
  (0, 0)	1
  (0, 755)	1
  (1, 0)	1
  (1, 693)	1
  (2, 0)	1
  (2, 92)	1
  (3, 0)	1
  (3, 335)	1
  (4, 1)	1
  (4, 715)	1
  (5, 1)	1
  (5, 222)	1
  (5, 659)	1
  (6, 1)	1
  (7, 1)	1
  (7, 32)	1
  (8, 1)	1
  (9, 1)	1
  (9, 32)	1
  (10, 1)	1
  (10, 319)	1
  (10, 709)	1
  (10, 772)	1
  (11, 1)	1
  (11, 66)	1
  :	:
  (530, 714)	1
  (531, 714)	1
  (532, 714)	1
  (533, 722)	1
  (534, 728)	1
  (534, 800)	1
  (535, 757)	1
  (535, 796)	1
  (536, 757)	1
  (536, 796)	1
  (537, 762)	1
  (538, 774)	1
  (539, 777)	1
  (540, 787)	1
  (540, 788)	1
  (541, 798)	1
  (542, 810)	1
  (543, 810)	1
  (544, 811)	1
  (545, 814)	1
  (546, 814)	1
  (547, 814)	1
  (548, 814)	1
  (549, 814)	1
  (550, 814)	1


We generate a network graph using pyvis that showcases our whole bipartite dataset at once, which is much more palatable to visualize as compared to the biadjacency matrix. Although we still have an extreme amount of nodes that makes it hard to make overall judgements, we will work on that further down the line.

We color the graph so that crime nodes will be shown in an easily separable green while those who are involved in crimes will be colored red if their gender was recorded as female or blue if their gender was recorded as male.


An interesting observations that we can get from this graph is the fact that for the most part there are few islands with the vast majority of crimes being connected to a main network. This indicates that in Moreno criminals are largely connected within vast networks rather than being isolated actors.

In [10]:
for n, d in G.nodes(data = True):
  if d["bipartite"] == "crime":
    G.nodes[n]["color"] = "green"
  elif d["gender"] == "female":
    G.nodes[n]["color"] = "red"
    G.nodes[n]["label"] = G.nodes[n]["name"]
    G.nodes[n]["title"] = G.nodes[n]["name"]
  else:
    G.nodes[n]["color"] = "blue"
    G.nodes[n]["label"] = G.nodes[n]["name"]
    G.nodes[n]["title"] = G.nodes[n]["name"]

We also add meaning to the color of the edges by having a color correspond to the role a person hade in the crime. The roles including a suspect, a victim, a witness, or a victim that is also a suspect.

In [11]:
c_dict = {'Suspect':"orange", 'Victim': "pink", 'Witness': "grey", 'Victim Suspect': "yellow"}
for e1, e2, d in G.edges(data = True):
  d["color"] = c_dict[d["role"]]

In [12]:
nt = Network(notebook = True, cdn_resources='in_line')
nt.from_nx(G)
nt.save_graph("moreno1.html")
HTML(filename="moreno1.html")

We add a small portion of the graph to be previewed below where we see crime 187 and 206 involving large amounts of people but mainly as witnesses. We can also see that there are some people such as Eddie McCann who work on crimes relatively alone.

In [13]:
from IPython.display import Image

Image(url=r"https://raw.githubusercontent.com/abnormalPotassium/DATA620/main/Project%202/moreno1.png", width=846, height=525)

---
## Bipartite Dataset Projection

Even if we only had one main connected component graph,we would still have 1263 nodes and the graph is in bipartite form, both of which make analysis difficult. To reduce the pain point of the graph being bipartite we will project a weighted graph for each of the types of nodes we have.
The persons graph `P` will have people nodes weighted by the amount of crimes that two people were involved in while the crimes graph `C` will have crime nodes weighted by the amount of people shared between the crimes.

In [14]:
P = bipartite.weighted_projected_graph(G, persons)
C = bipartite.weighted_projected_graph(G, crimes)

We generate the projected people graph below and there are a few things that come to mind: The graph is more ordered and has less nodes to look through, but there are many areas where we get balls of yarn from the overlap of people. So, additional pruning is needed to better analyze this graph and pick out people of interest. Additionally, those with weighted connections are actually relatively rare meaning most people do not commit crimes with the same accomplices multiple times. Instead they are more likely to have weak connections to be connected to others that are comitting crimes in the Morena crime data. Finally, we are able to see pockets of interconnected crime which could indicate organized crime that is taking place.

In [15]:
nt = Network(notebook = True, cdn_resources='in_line')
nt.from_nx(P)
nt.save_graph("moreno2.html")
HTML(filename="moreno2.html")

We showcase an image example of the projected people graph below.

In [16]:
Image(url=r"https://raw.githubusercontent.com/abnormalPotassium/DATA620/main/Project%202/moreno2.png", width=900, height=600)

The projected crime graph is surprisingly even more interesting and readable than the people graph due to having less nodes. We can see more distinct pockets of yarn where the crimes have strings of interconnected people involved together in each of these crimes. I'd wager that the crimes that are in these pockets are definitely organized criminal activity in some way or form.

In [17]:
nt = Network(notebook = True, cdn_resources='in_line')
nt.from_nx(C)
nt.save_graph("moreno3.html")
HTML(filename="moreno3.html")

An example image of the projected crime graph is displayed below.

In [18]:
Image(url=r"https://raw.githubusercontent.com/abnormalPotassium/DATA620/main/Project%202/moreno3.png", width=900, height=600)

---
## Dataset Size Reduction

Right now our dataset and graphs are quite large and thus hard to analyze. To help further analysis of the crimes and people involved we want to pare down our dataset to those important groups.

If we look below at the component subgraph lengths that we have within our data we can see that there is one large interconnected subgraph that we want to focus on. The other subgraphs largely consist of diad or triad islands which aren't going to be very insightful.

In [19]:
print([len(c) for c in sorted(nx.connected_components(P), key=len, reverse=True)],
      [len(c) for c in sorted(nx.connected_components(C), key=len, reverse=True)])

[754, 22, 11, 8, 8, 4, 4, 3, 3, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] [509, 8, 7, 5, 3, 3, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]


We extract the subgraphs with largest amount of nodes and create copies of them that will now be the larger graphs which we focus on. As we can see below the subgraphs with just a few connected components are no longer present.

In [20]:
P = P.subgraph(max(nx.connected_components(P), key=len)).copy()
C = C.subgraph(max(nx.connected_components(C), key=len)).copy()
print([len(c) for c in sorted(nx.connected_components(P), key=len, reverse=True)],
      [len(c) for c in sorted(nx.connected_components(C), key=len, reverse=True)])

[754] [509]


The island method helps us further restrict the nodes we're looking at to those which would be of high importance in our dataset. We modify code from the book Social Network Analysis for Startups by  Maksim Tsvetovat and Alexander Kouznetsov for this algorithm.

The first piece of the algorithm is to remove edges that don't meet a certain requirement, in this case where the edges are not weighted by a certain amount.

In [21]:
def trim_edges(g, weight=1):
        g2=nx.Graph()
        for f, to, edata in g.edges(data=True):
                if edata['width'] > weight:
                        g2.add_edge(f,to,**edata)
        return g2

The `trim_edges` function is then replicated for multiple iterations within our `island_method` function which creates an integer number of steps to change the threshold by from the minimum weight to the maximum weight.

In [22]:
def island_method(g, iterations=5):
    weights= [edata['width'] for f,to,edata in g.edges(data=True)]

    mn=int(min(weights))
    mx=int(max(weights))
    #compute the size of the step, so we get a reasonable step in iterations
    step=int((mx-mn)/iterations)
    if step == 0:
      step = 1

    return [[threshold, trim_edges(g, threshold)] for threshold in range(mn,mx,step)]

Upon applying the algorithm to our projected people data we see that our initial assessment of there being relatively few high weight connections was correct. The majority of people are connected only by a single crime, while there are only 4 crimes that people are connected by at max for our top island.

In [23]:
people_islands=island_method(P)
print("lv sz cn")
for i in people_islands:
  # print the threshold level, size of the graph, and number of connected components
  print(i[0], len(i[1]), len([len(c) for c in sorted(nx.connected_components(i[1]), key=len, reverse=True)]))

lv sz cn
1 89 27
2 28 12
3 15 7
4 6 3


Upon applying the algorithm to our projected criminal data we see that there is an extremely low amount of crimes that are commited by the same people. Only having 10 nodes where a crime is connected by more than two people.

In [24]:
crime_islands=island_method(C)
print("lv sz cn")
for i in crime_islands:
  # print the threshold level, size of the graph, and number of connected components
  print(i[0], len(i[1]), len([len(c) for c in sorted(nx.connected_components(i[1]), key=len, reverse=True)]))

lv sz cn
1 117 35
2 10 3


---
## Reduced Size Projection Analysis

Taking the top islands of our projected graphs we plot them starting with the projected people graph that has to have its attributes redefined below.

In [25]:
for n, d in people_islands[3][1].nodes(data = True):
  if G.nodes[n]["gender"] == "female":
    people_islands[3][1].nodes[n]["color"] = "red"
    people_islands[3][1].nodes[n]["label"] = G.nodes[n]["name"]
    people_islands[3][1].nodes[n]["title"] = G.nodes[n]["name"]
  else:
    people_islands[3][1].nodes[n]["color"] = "blue"
    people_islands[3][1].nodes[n]["label"] = G.nodes[n]["name"]
    people_islands[3][1].nodes[n]["title"] = G.nodes[n]["name"]

We have 3 disparate pairs with a weight of 4 shared crimes between them. Surprisingly there is no obvious familial relation such as a family last name. However, with 4 crimes shared between everyone in this graph there is no doubt that they have some form of partnership in crime.

In [26]:
nt = Network(notebook = True, cdn_resources='in_line')
nt.from_nx(people_islands[3][1])
nt.save_graph("moreno4.html")
HTML(filename="moreno4.html")

Below is an image of the graph.

In [27]:
Image(url=r"https://raw.githubusercontent.com/abnormalPotassium/DATA620/main/Project%202/moreno4.png", width=1500, height=600)

Our crimes with a weight of two don't have names or gender attached to them, but we are able to see a web of multiple crimes taking place that have at least two people shared between each crime. If we could establish any crimes as being organized from our data it would certainly be the crimes that belong in this connected subgraph.

In [28]:
nt = Network(notebook = True, cdn_resources='in_line')
nt.from_nx(crime_islands[1][1])
nt.save_graph("moreno5.html")
HTML(filename="moreno5.html")

Below is an image of the graph.

In [29]:
Image(url=r"https://raw.githubusercontent.com/abnormalPotassium/DATA620/main/Project%202/moreno5.png", width=1500, height=600)

Let's say we wanted to catch the members of this crime ring. If we call the neighbors of these crimes in the original graph we're able to see who was taking part in these various crimes. Luella Katz, Catherine Steiner, and Grant Mitchell in particular seem to be troublesome individuals within Moreno and part of organized crime as they're not only part of this crime ring but were in the highest weighted people nodes as well.

In [30]:
for n in crime_islands[1][1].nodes():
  if n not in ["c28","c43","c108","c104"]:
    print(n, [G.nodes[g]['name'] for g in G.neighbors(n)])

c59 ['Pearl Armstrong', 'Luella Katz', 'Cyndi Powell', 'Catherine Steiner']
c419 ['Justin Johnston', 'Luella Katz', 'Cyndi Powell', 'Catherine Steiner']
c95 ['Chris Bender', 'Carson Bixby', 'Charlie Bradley', 'James Bulwer', 'Alice Frost', 'Robert Harrison', 'Jill Jenkins', 'Justin Johnston', 'Luella Katz', 'Owen Kirkland', 'Bradley Marcus', 'Felix Resnick', 'Thomas Michael Smith']
c417 ['Justin Johnston', 'Luella Katz', 'Thomas Michael Smith', 'Catherine Steiner']
c110 ['Lee Jerry Bendix', 'Sharon Bendix', 'Errol Binder', 'Felecia Cantwell', 'Brendan Jackson', 'Luella Katz', 'Grant Mitchell', 'Lyle Mobley', 'Byron Parker', 'Thomas Michael Smith', 'Catherine Steiner', 'Marcia Thomas', 'Ronnell Valet', 'Jackie Vanese', 'Hiroko Vest', 'Irma Vest', 'Irwin Vest', 'Roosevelt Williams']
c196 ['Felecia Cantwell', 'Grant Mitchell', 'Lyle Mobley']


Now if we want to see which people had the highest degree in our projected graph to figure out who might be the most connected in the Moreno underworld we once again see Luella Katz pop up. Going to her probably would bring good data for the crime activity in Moreno.

In [31]:
sortw = sorted(P.degree, key=lambda x: x[1], reverse=True)
print("Top 5 # of Partners")
for w,n in sortw[:5]:
  w = G.nodes[w]["name"]
  print(f"{n} {w}")

Top 5 # of Partners
51 Luella Katz
48 Chad Abrams
44 Bud Hemphill
33 Lee Jerry Bendix
33 Thomas Michael Smith


Finally, if we take a look at the crimes with the highest degree of centrality we see that crime c110 seems to connect most people who crime together and would be good to look into the details for possibly determining how these criminals came together.

In [32]:
sortw = sorted(C.degree, key=lambda x: x[1], reverse=True)
print("Top 5 # connected crimes")
for w,n in sortw[:5]:
  print(f"{n} {w}")

Top 5 # connected crimes
75 c110
39 c23
39 c47
35 c95
34 c14


---
## Video Presentation

The code below allows a YouTube link to the video presentation to be inserted for the url variable and will then display the YouTube video within the notebook itself.

A regex match extracts the video ID from the URL which is then fed into the IPython package's built in Youtube embedder.

In [35]:
url = "https://youtu.be/rHYWU1Dpr1k"

In [36]:
from IPython.display import YouTubeVideo
import re

reg = r"(?:v=|\/)([0-9A-Za-z_-]{11}).*"
urlid = re.search(reg, url)[1]

YouTubeVideo(urlid, width=800, height=450)